In [1]:
import os
from PIL import Image
import numpy as np
import sys

In [2]:
def get_image_matrix(image_path):
    img = Image.open(image_path)
    return np.asarray(img, dtype=np.float32)


def get_mask_matrix(mask_path):
    mask = Image.open(mask_path)
    return np.asarray(mask, dtype=np.int64)

In [6]:
np.set_printoptions(threshold=sys.maxsize)
img_path = "D:/Users/Sime/FER/Diplomski/Diplomski rad/Kapsularne/Retinal-fluid-segmentation/Cirrus_1e0e71d2acdc57f10ab6712ab87b2ef7_000.jpg"
img = Image.open(img_path).convert('L')
img = img.resize((256, 512))
img.save('manja.jpg')
train_img_int = np.array(img, dtype=np.uint8)
print(train_img_int)

[[[ 25  25  25]
  [ 66  66  66]
  [ 49  49  49]
  [ 42  42  42]
  [ 61  61  61]
  [ 51  51  51]
  [ 26  26  26]
  [ 45  45  45]
  [ 45  45  45]
  [ 35  35  35]
  [ 28  28  28]
  [  0   0   0]
  [ 40  40  40]
  [ 54  54  54]
  [ 58  58  58]
  [ 54  54  54]
  [ 61  61  61]
  [ 56  56  56]
  [ 60  60  60]
  [ 47  47  47]
  [ 49  49  49]
  [ 81  81  81]
  [112 112 112]
  [ 81  81  81]
  [ 84  84  84]
  [ 96  96  96]
  [ 42  42  42]
  [ 33  33  33]
  [ 42  42  42]
  [ 35  35  35]
  [ 37  37  37]
  [ 61  61  61]
  [ 33  33  33]
  [ 37  37  37]
  [ 37  37  37]
  [ 19  19  19]
  [ 35  35  35]
  [ 69  69  69]
  [ 26  26  26]
  [ 14  14  14]
  [ 15  15  15]
  [ 30  30  30]
  [ 30  30  30]
  [ 15  15  15]
  [ 52  52  52]
  [ 28  28  28]
  [ 17  17  17]
  [ 17  17  17]
  [ 35  35  35]
  [ 47  47  47]
  [  0   0   0]
  [ 13  13  13]
  [ 24  24  24]
  [ 30  30  30]
  [ 30  30  30]
  [ 49  49  49]
  [ 61  61  61]
  [ 45  45  45]
  [ 28  28  28]
  [ 21  21  21]
  [ 40  40  40]
  [ 33  33  33]
  [ 33  

In [7]:
train_img_float = np.array(img, dtype=np.float32)
print(train_img_float)

[[[ 25.  25.  25.]
  [ 66.  66.  66.]
  [ 49.  49.  49.]
  [ 42.  42.  42.]
  [ 61.  61.  61.]
  [ 51.  51.  51.]
  [ 26.  26.  26.]
  [ 45.  45.  45.]
  [ 45.  45.  45.]
  [ 35.  35.  35.]
  [ 28.  28.  28.]
  [  0.   0.   0.]
  [ 40.  40.  40.]
  [ 54.  54.  54.]
  [ 58.  58.  58.]
  [ 54.  54.  54.]
  [ 61.  61.  61.]
  [ 56.  56.  56.]
  [ 60.  60.  60.]
  [ 47.  47.  47.]
  [ 49.  49.  49.]
  [ 81.  81.  81.]
  [112. 112. 112.]
  [ 81.  81.  81.]
  [ 84.  84.  84.]
  [ 96.  96.  96.]
  [ 42.  42.  42.]
  [ 33.  33.  33.]
  [ 42.  42.  42.]
  [ 35.  35.  35.]
  [ 37.  37.  37.]
  [ 61.  61.  61.]
  [ 33.  33.  33.]
  [ 37.  37.  37.]
  [ 37.  37.  37.]
  [ 19.  19.  19.]
  [ 35.  35.  35.]
  [ 69.  69.  69.]
  [ 26.  26.  26.]
  [ 14.  14.  14.]
  [ 15.  15.  15.]
  [ 30.  30.  30.]
  [ 30.  30.  30.]
  [ 15.  15.  15.]
  [ 52.  52.  52.]
  [ 28.  28.  28.]
  [ 17.  17.  17.]
  [ 17.  17.  17.]
  [ 35.  35.  35.]
  [ 47.  47.  47.]
  [  0.   0.   0.]
  [ 13.  13.  13.]
  [ 24.  24.

In [1]:
import keras.backend as K

Using TensorFlow backend.


In [13]:
def calculate_class_weights_presence(root_path):
    masks_path = root_path + "/masks"
    masks = [d for d in os.listdir(masks_path)]
    class_counter = [0, 0, 0, 0]

    for m in masks:
        mask = Image.open(os.path.join(root_path, 'masks', m))
        pixels = mask.getdata()
        if 0 in pixels:
            class_counter[0] += 1
        if 85 in pixels:
            class_counter[1] += 1
        if 170 in pixels:
            class_counter[2] += 1
        if 255 in pixels:
            class_counter[3] += 1

    print(class_counter)
    class_weights = {
        0: class_counter[0]/class_counter[0],
        1: class_counter[0]/class_counter[1],
        2: class_counter[0] / class_counter[2],
        3: class_counter[0] / class_counter[3]
    }
    return  class_weights


In [12]:
def calculate_class_weights_pixel_wise(root_path):
    masks_path = root_path + "/masks"
    masks = [d for d in os.listdir(masks_path)]
    class_counter = [0, 0, 0, 0]

    for m in masks:
        mask = Image.open(os.path.join(root_path, 'masks', m))
        pixels = mask.getdata()
        for p in pixels:
            if p == 0:
                class_counter[0] += 1
            if p == 85:
                class_counter[1] += 1
            if p == 170:
                class_counter[2] += 1
            if p == 255:
                class_counter[3] += 1

    print(class_counter)
    class_weights = {
        0: class_counter[0] / class_counter[0],
        1: class_counter[0] / class_counter[1],
        2: class_counter[0] / class_counter[2],
        3: class_counter[0] / class_counter[3]
    }
    return class_weights

In [15]:
root_path = "D:/Users/Sime/FER/Diplomski/Diplomski rad/Kapsularne/Retinal-fluid-segmentation/imgs/retouch_data/Cirrus"
class_weights = calculate_class_weights_presence(root_path)
print(class_weights)

[3072, 935, 700, 622]
{0: 1.0, 1: 3.2855614973262033, 2: 4.388571428571429, 3: 4.938906752411576}
